In [7]:
# Standard library imports
import sys
import os
from pathlib import Path

# Add the path to 'database_functions.py'
path = Path('..', '002_database-functions')
sys.path.append(str(path))

# Third-party library imports
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from plotly.io import write_image
import json
import requests

# Custom module imports
import database_functions as func
from eda_functions import choropleth

# Configure inline plotting for Jupyter
%matplotlib inline


# Create a Database instance
path = r'008_supplemental\002_clean-data'
db = func.Database(path)
print("Database initialized successfully.")
# Assuming db is your Database instance

Database initialized successfully.


In [14]:
db.facility_records()

year     cnn                                          fac_name  \
0      2018.0  552777                       LAUREL CANYON DIALYSIS, LLC   
1      2018.0   52812                        FMC-BLYTHE DESERT DIALYSIS   
2      2018.0   52811                   DAVITA SAN LUIS OBISPO DIALYSIS   
3      2018.0   52810                           DAVITA BENICIA DIALYSIS   
4      2018.0   52839                         DAVITA NORTHEAST DIALYSIS   
...       ...     ...                                               ...   
37736  2024.0  552816                Ontario Holt Dialysis Center, Inc.   
37737  2024.0   52305              SANTA CLARA VALLEY RENAL CARE CENTER   
37738     NaN   50327              LOMA LINDA UNIVERSITY MEDICAL CENTER   
37739     NaN   50140  KAISER FOUNDATION HOSPITAL MEDICAL CTR.- FONTANA   
37740     NaN  552534              COLUSA INDIAN HEALTH CLINIC DIALYSIS   

           county_name  stations     prof_np chain_own  \
0          Los Angeles        30      profit        no   
1            Riverside        13      profit       yes   
2      San Luis Obispo        20      profit       yes   
3               Solano        14      profit       yes   
4                 Kern        38      profit       yes   
...                ...       ...         ...       ...   
37736   San Bernardino        28      profit        no   
37737      Santa Clara        25  non_profit        no   
37738   San Bernardino         5  non_profit        no   
37739   San Bernardino         5  non_profit       yes   
37740           Colusa         6  non_profit        no   

                    chain_org  mortality_rate_facility  \
0                 INDEPENDENT                     22.8   
1      FRESENIUS MEDICAL CARE                     33.8   
2                      DAVITA                     22.8   
3                      DAVITA                     24.2   
4                      DAVITA                     25.2   
...                       ...                      ...   
37736             Independent                     29.8   
37737             Independent                     19.8   
37738             INDEPENDENT                      NaN   
37739       KAISER PERMANENTE                      9.1   
37740             INDEPENDENT                      6.9   

       readmission_rate_facility  ... survey_count  survey_rate  fac_star  \
0                           33.9  ...         65.0          NaN       4.0   
1                           21.8  ...          NaN          NaN       NaN   
2                           27.1  ...          NaN          NaN       NaN   
3                           24.9  ...         54.0          NaN       3.0   
4                           27.5  ...         40.0          NaN       5.0   
...                          ...  ...          ...          ...       ...   
37736                       31.0  ...         45.0         25.0       4.0   
37737                       25.3  ...         47.0         19.0       3.0   
37738                        9.4  ...          NaN          NaN       NaN   
37739                       34.4  ...          NaN          NaN       NaN   
37740                        NaN  ...          NaN          NaN       NaN   

       xp_star  comm_scr  quality_scr  info_scr  phys_scr  staff_scr  fac_scr  
0          NaN      87.0         82.0      85.0      88.0       88.0     89.0  
1          NaN       NaN          NaN       NaN       NaN        NaN      NaN  
2          NaN       NaN          NaN       NaN       NaN        NaN      NaN  
3          NaN      90.0         81.0      83.0      89.0       86.0     87.0  
4          NaN      88.0         89.0      87.0      88.0       93.0     94.0  
...        ...       ...          ...       ...       ...        ...      ...  
37736      3.0      79.0         82.0      72.0      81.0       89.0     90.0  
37737      4.0      85.0         85.0      81.0      88.0       88.0     89.0  
37738      NaN       NaN          NaN       NaN       NaN        NaN 

# Facility Records Dataset

## Task 1: Basic statistics and data overview of the 'fascility records' table

In [17]:

def load_fascility_records(db=None):
    
    if db is None:
        db = func.Database()
        
    # Load the fascility_records table
    fasility_records_df = db.facility_records()

    # remove '_1' from the column names, '_1' was added to the column names to avoid conflicts with the column names from aggregated fasciltiy table
    fasility_records_df.columns = [col.replace('_1', '') for col in fasility_records_df.columns]

    # cast mortality_rate_facility and readmission_rate_facility to numeric
    fasility_records_df['mortality_rate_facility'] = pd.to_numeric(fasility_records_df['mortality_rate_facility'], errors='coerce')   
    fasility_records_df['readmission_rate_facility'] = pd.to_numeric(fasility_records_df['readmission_rate_facility'], errors='coerce')
    
    # rename patient_hospital_readmission_category column
    fasility_records_df.rename(columns={'patient_hospital_readmission_category': 'readmission_category'}, inplace=True)
    
    view_columns = ['year', 'county_name', 'stations', 'prof_np', 'chain_own', 'chain_org', 'mortality_rate_facility', 'readmission_rate_facility', 'readmission_category', 'fac_star', 'xp_star', 'staff_scr']
    db.facility_records.add_view('quality_of_care', view_columns)
    # Sort the dataframe by year and county_name
    fasility_records_df = db.facility_records.quality_of_care.sort_values(['year', 'county_name']).reset_index(drop=True)

    return fasility_records_df

fasility_records_df = load_fascility_records(db)
print(fasility_records_df.describe().T)

                             count         mean       std     min     25%  \
year                       37738.0  2021.027717  1.979136  2018.0  2019.0   
stations                   37741.0    20.639517  9.508625     0.0    16.0   
mortality_rate_facility    35434.0    21.802489  6.728506     0.0    17.6   
readmission_rate_facility  35342.0    26.576122  7.373863     0.0    22.1   
fac_star                   23504.0     3.663802  0.957137     1.0     3.0   
xp_star                    19895.0     3.611058  0.814083     1.0     3.0   
staff_scr                  23504.0    87.284717  3.733921    70.0    85.0   

                              50%     75%     max  
year                       2021.0  2023.0  2024.0  
stations                     21.0    25.0    76.0  
mortality_rate_facility      21.0    24.9    83.5  
readmission_rate_facility    26.6    30.9    70.6  
fac_star                      4.0     4.0     5.0  
xp_star                       4.0     4.0     5.0  
staff_scr          

## Task 2: Visualize Pairwise Relationships of Quality of Care Metrics by Chain Ownership

In [18]:
# Select the columns to be used in the pairplot
all_columns = ['year', 'stations','mortality_rate_facility', 'readmission_rate_facility', 'fac_star', 'xp_star', 'staff_scr']
var_columns = ['mortality_rate_facility', 'readmission_rate_facility']

# Create the pairplot with the filtered columns
g = sns.pairplot(data=fasility_records_df, vars=var_columns, hue='prof_np')

# Add a title to the entire pairplot
g.fig.suptitle("Pairwise Relationships of Quality of Care Metrics by Chain Ownership", 
               fontsize=16, y=1.02)

Text(0.5, 1.02, 'Pairwise Relationships of Quality of Care Metrics by Chain Ownership')

## Task 3: Pairwise Relationships of Quality of Care Metrics by Chain Ownership

In [19]:
# Select the columns to be used in the pairplot
all_columns = ['year', 'stations','mortality_rate_facility', 'readmission_rate_facility', 'fac_star', 'xp_star', 'staff_scr']
var_columns = ['mortality_rate_facility', 'readmission_rate_facility']

# Create the pairplot with the filtered columns
g = sns.pairplot(data=fasility_records_df, vars=var_columns, hue='chain_own')

# Add a title to the entire pairplot
g.fig.suptitle("Pairwise Relationships of Quality of Care Metrics by Chain Ownership", 
               fontsize=16, y=1.02)

Text(0.5, 1.02, 'Pairwise Relationships of Quality of Care Metrics by Chain Ownership')

# Aggregated Fascility Dataset

## Task 1: Basic statistics and data overview of the 'fascility' table

In [20]:
# Load aggregated fascility table
facility_agg = db.facility()
facility_agg.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 316 entries, 0 to 315
Data columns (total 19 columns):
 #   Column                                 Non-Null Count  Dtype  
---  ------                                 --------------  -----  
 0   county_name                            316 non-null    object 
 1   year                                   316 non-null    int64  
 2   fac_count                              316 non-null    int64  
 3   stations                               316 non-null    int64  
 4   prof_np                                316 non-null    float64
 5   chain_own                              316 non-null    float64
 6   survey_count                           316 non-null    int64  
 7   survey_rate                            78 non-null     float64
 8   fac_star                               275 non-null    float64
 9   xp_star                                234 non-null    float64
 10  comm_scr                               275 non-null    float64
 11  qualit

In [25]:

def load_fascility_coverage(db=None):
    
    if db is None:
        db = func.Database()
        
    # Create covereage view for facility table
    coverage_columns = ['year', 'county_name', 'fac_count', 'stations', 'prof_np', 'chain_own']
    db.facility.add_view('coverage', coverage_columns)
    
    # Create user_count view for medicare table
    user_count_columns = ['year', 'county_name', 'user_cnt']
    db.medicare.add_view('user_count', user_count_columns)
    
    # Merge the coverage and user_count views
    df = db.merge_views([('facility', 'coverage'), ('medicare', 'user_count')]).copy()
    
    # Create per capita stations column
    df['stations_per_capita'] = df['stations'] / df['user_cnt']
    
    # Constriaints to Year 2018-2022
    df = df[(df['year'] >= 2018) & (df['year'] <= 2022)]

    # Sort the dataframe by year and county_name
    df.sort_values(['year', 'county_name'])
    df.reset_index(drop=True)

    return df

facility_coverage_df = load_fascility_coverage(db)
print(facility_coverage_df.head())

    county_name  year  fac_count  stations   prof_np  chain_own  user_cnt  \
0       Alameda  2018      240.0    4733.0  0.820833        1.0    1455.0   
1         Butte  2018       32.0     584.0  0.750000        1.0     285.0   
2      Columbia  2018        2.0      26.0  1.000000        1.0       NaN   
3  Contra Costa  2018      137.0    2690.0  0.985401        1.0    1002.0   
4     El Dorado  2018        8.0     185.0  1.000000        1.0     125.0   

   stations_per_capita  
0             3.252921  
1             2.049123  
2                  NaN  
3             2.684631  
4             1.480000  


In [28]:
stations_per_capita = facility_coverage_df[['year','county_name', 'stations_per_capita']]
stations_per_capita_melted = pd.melt(stations_per_capita, id_vars=['county_name'], var_name='year', value_name='percentage')


fig = choropleth(data=facility_coverage_df, hue_column='stations_per_capita', slider_column='year', title=f'Stations per by County in California')
fig.show()

# Get the output path
current_dir = os.path.dirname(os.path.abspath('__file__'))
project_root = os.path.abspath(os.path.join(current_dir, '..', '..', '..'))
visualizations_dir = os.path.join(project_root, '007_visualizations')
output_path = os.path.join(visualizations_dir, f'Interactive_stations_per_capita_choropleth.html')
fig.write_html(output_path)

In [27]:
stations_per_capita = facility_coverage_df[['year','county_name', 'stations_per_capita']]
ballot_years = [2018, 2020, 2022]

# Get the output path
current_dir = os.path.dirname(os.path.abspath('__file__'))
project_root = os.path.abspath(os.path.join(current_dir, '..', '..', '..'))
visualizations_dir = os.path.join(project_root, '007_visualizations')



for year in ballot_years:
    plot_df = stations_per_capita[stations_per_capita['year'] == year]
    output_path = os.path.join(visualizations_dir, f'{year}_stations_per_capita_choropleth.html')
    fig = choropleth(data=plot_df, hue_column='stations_per_capita', title=f'Stations per by County in California in {year}')
    fig.show()
    fig.write_html(output_path)


c:\Users\kasra\OneDrive\Desktop\Code\MSI\milestone_1\005_data-analysis-scripts\002_exploratory-analysis\003_exploratory-data-analysis\eda_functions.py:37: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



c:\Users\kasra\OneDrive\Desktop\Code\MSI\milestone_1\005_data-analysis-scripts\002_exploratory-analysis\003_exploratory-data-analysis\eda_functions.py:37: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



c:\Users\kasra\OneDrive\Desktop\Code\MSI\milestone_1\005_data-analysis-scripts\002_exploratory-analysis\003_exploratory-data-analysis\eda_functions.py:37: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

